In [94]:
from pyspark.sql import SparkSession
import pyspark.pandas as ps
import pandas as pd
import numpy as np
import datetime
import collections
# spark = SparkSession\
#     .builder\
#     .appName("MergeDataset")\
#     .getOrCreate()

In [81]:
player_attr = pd.read_csv('./data/player_attr.csv')
fbref_MatchPlayerStats = pd.read_csv('./data/fbref_MatchPlayerStats.csv')
fbref_MatchInfos = pd.read_csv('./data/fbref_MatchInfos.csv')

In [82]:
fbref_MatchInfos['match_date'].astype('datetime64[ns]')

0      2019-05-12
1      2020-07-26
2      2020-07-26
3      2020-07-26
4      2020-07-26
          ...    
1985   2022-08-06
1986   2022-08-06
1987   2022-08-06
1988   2022-08-06
1989   2022-08-05
Name: match_date, Length: 1990, dtype: datetime64[ns]

In [83]:
list_names = ['Troy','Deeney']

len([all(name in player_name for name in list_names) for player_name in player_attr['player_full_name'].tolist()])
len(player_attr)

85427

In [123]:
def MergedSoFifaFbref_old(fbref_MatchInfos,fbref_MatchPlayerStats,player_attr):
    fbref_players = fbref_MatchPlayerStats[['player_kitnum','player_name','position','team','nationality','fbrefMatchId','age']]
    fbref_players = fbref_players.merge(fbref_MatchInfos[['match_date','fbrefMatchId']], on='fbrefMatchId', how = 'inner')
    fbref_players['player_name'] = fbref_players['player_name'].astype('str')
    fbref_players['match_date'] = fbref_players['match_date'].astype('datetime64[ns]')
    player_attr['update_date'] = player_attr['update_date'].astype('datetime64[ns]')
    fbref_players['age'] = fbref_players['age'].astype('str')
    columns_MergedSoFifaFbref = fbref_players.columns.values.tolist()
    columns_MergedSoFifaFbref.extend(player_attr.columns.values.tolist())
    columns_MergedSoFifaFbref = np.unique(columns_MergedSoFifaFbref).tolist()
    MergedSoFifaFbref = pd.DataFrame(columns=columns_MergedSoFifaFbref)
    for i in range(0,len(fbref_players)):
    # for i in range(0,3):
        fbref_player = fbref_players.loc[i]
        fbref_player_name = fbref_player['player_name']
        fbref_player_name = fbref_player_name.split(' ')
        match_date = fbref_player['match_date']
        player_kitnum = fbref_player['player_kitnum']
        team = fbref_player['team']
        age = fbref_player['age']
        age = age[0:2]
        
        rows_contain_name = [all(name in player_full_name for name in fbref_player_name) for player_full_name in player_attr['player_full_name'].tolist()]
        df_sofifa = player_attr[rows_contain_name]
        df_sofifa = df_sofifa[(df_sofifa['update_date'].dt.month == match_date.month) & (df_sofifa['update_date'].dt.year == match_date.year)]
        # df_sofifa = df_sofifa[df_sofifa['team1_kitnum'] == player_kitnum]
        df_sofifa = df_sofifa[df_sofifa['team1'] == team]
        df_sofifa = df_sofifa[df_sofifa['age'] == age]
        if (len(df_sofifa)==1):
            MergedSoFifaFbref_row = df_sofifa.iloc[0:1]
            delete_columns = fbref_players.columns.values.tolist()
            delete_columns.extend(MergedSoFifaFbref_row.columns.values.tolist())
            delete_columns = [item for item, count in collections.Counter(delete_columns).items() if count > 1]
            MergedSoFifaFbref_row = MergedSoFifaFbref_row.drop(columns = delete_columns)
            MergedSoFifaFbref_row.reset_index(drop=True, inplace=True)
            MergedSoFifaFbref_row = pd.concat([MergedSoFifaFbref_row.reset_index(drop=True),fbref_players.iloc[i:i+1].reset_index(drop=True)],axis=1)
        else:
            MergedSoFifaFbref_row = fbref_player.iloc[i:i+1]
        MergedSoFifaFbref.reset_index(inplace=True, drop=True)
        MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])
        
    MergedSoFifaFbref.to_csv('./data/MergedSoFifaFbref.csv',index=False,header=True,encoding='utf-8-sig')

MergedSoFifaFbref_old(fbref_MatchInfos,fbref_MatchPlayerStats,player_attr)

   acceleration  aggression  agility all_positions attacking_work_rate  \
0            54          85       62            ST                High   

   balance  ball_control    birthday         body_type  composure  ...  \
0       71            77  1988-06-29  Stocky (170-185)       78.0  ...   

   weak_foot  weight  player_kitnum  player_name  position     team  \
0          3      90            9.0  Troy Deeney        FW  Watford   

   nationality  fbrefMatchId     age  match_date  
0          ENG      db4d7668  30-317  2019-05-12  

[1 rows x 75 columns]
   acceleration  aggression  agility all_positions attacking_work_rate  \
0            89          40       94      CF RW LW                High   

   balance  ball_control    birthday         body_type  composure  ...  \
0       77            86  1994-03-13  Normal (170-185)       77.0  ...   

   weak_foot  weight  player_kitnum      player_name  position     team  \
0          4      73            7.0  Gerard Deulofeu        F

C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])


   acceleration  aggression  agility all_positions attacking_work_rate  \
0            68          70       71     CAM RM CM              Medium   

   balance  ball_control    birthday    body_type  composure  ...  weak_foot  \
0       75            80  1995-04-17  Lean (185+)       78.0  ...          3   

   weight  player_kitnum  player_name  position     team  nationality  \
0      74           19.0  Will Hughes     AM,RM  Watford          ENG   

   fbrefMatchId     age  match_date  
0      db4d7668  24-025  2019-05-12  

[1 rows x 75 columns]
   acceleration  aggression  agility all_positions attacking_work_rate  \
0            63          66       63         LB LM              Medium   

   balance  ball_control    birthday      body_type  composure  ...  \
0       43            70  1994-01-02  Normal (185+)       72.0  ...   

   weak_foot  weight  player_kitnum  player_name  position     team  \
0          3      87           11.0  Adam Masina        LB  Watford   

   nation

C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of array concatenation with empty entries is deprecated. In a future version, this will no longer exclude empty items when determining the result dtype. To retain the old behavior, exclude the empty entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])
C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])


   acceleration  aggression  agility all_positions attacking_work_rate  \
0            40          73       59            CB              Medium   

   balance  ball_control    birthday    body_type  composure  ...  weak_foot  \
0       54            59  1989-02-06  Lean (185+)       71.0  ...          3   

   weight  player_kitnum     player_name  position     team  nationality  \
0      83           15.0  Craig Cathcart     CB,LB  Watford          NIR   

   fbrefMatchId     age  match_date  
0      db4d7668  30-095  2019-05-12  

[1 rows x 75 columns]
   acceleration  aggression  agility all_positions attacking_work_rate  \
0            66          78       60            CB              Medium   

   balance  ball_control    birthday    body_type  composure  ...  weak_foot  \
0       58            66  1991-02-24  Lean (185+)       64.0  ...          3   

   weight  player_kitnum         player_name  position     team  nationality  \
0      84           27.0  Christian Kabasele    

...

   acceleration  aggression  agility all_positions attacking_work_rate  \
0            66          77       71           CDM              Medium   

   balance  ball_control    birthday       body_type  composure  ...  \
0       70            67  1993-03-09  Lean (170-185)       73.0  ...   

   weak_foot  weight  player_kitnum  player_name  position          team  \
0          3      72           19.0  Tom Trybull     DM,CM  Norwich City   

   nationality  fbrefMatchId     age  match_date  
0          GER      464461f5  26-259  2019-11-23  

[1 rows x 75 columns]
   acceleration  aggression  agility all_positions attacking_work_rate  \
0            62          80       68           CDM              Medium   

   balance  ball_control    birthday         body_type  composure  ...  \
0       74            63  1986-04-04  Normal (170-185)       65.0  ...   

   weak_foot  weight  player_kitnum       player_name  position          team  \
0          2      68           27.0  Alexander Te

C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of array concatenation with empty entries is deprecated. In a future version, this will no longer exclude empty items when determining the result dtype. To retain the old behavior, exclude the empty entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])
C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of array concatenation with empty entries is deprecated. In a future version, this will no longer exclude empty items when determining the result dtype. To retain the old behavior, exclude the empty entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])
C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of array concatenation with empty entries is deprecated. In a future version, this will no

   acceleration  aggression  agility all_positions attacking_work_rate  \
0            74          80       72            ST                High   

   balance  ball_control    birthday      body_type  composure  ...  \
0       49            78  1991-05-05  Normal (185+)       78.0  ...   

   weak_foot  weight  player_kitnum   player_name  position  \
0          4      81            9.0  Raúl Jiménez        FW   

                      team  nationality  fbrefMatchId     age  match_date  
0  Wolverhampton Wanderers          MEX      219643bc  28-202  2019-11-23  

[1 rows x 75 columns]
   acceleration  aggression  agility all_positions attacking_work_rate  \
0            88          61       82           LWB                High   

   balance  ball_control    birthday       body_type  composure  ...  \
0       80            77  1999-04-09  Lean (170-185)       74.0  ...   

   weak_foot  weight  player_kitnum    player_name  position  \
0          2      64           29.0  Rúben Vinag

C:\Users\super\AppData\Local\Temp\ipykernel_12644\1594320754.py:40: FutureWarning: The behavior of array concatenation with empty entries is deprecated. In a future version, this will no longer exclude empty items when determining the result dtype. To retain the old behavior, exclude the empty entries before the concat operation.
  MergedSoFifaFbref = pd.concat([MergedSoFifaFbref,MergedSoFifaFbref_row])


KeyboardInterrupt: 

In [ ]:
def MergedSoFifaFbref(fbref_MatchInfos,fbref_MatchPlayerStats,player_attr):
    fbref_players = fbref_MatchPlayerStats[['player_kitnum','player_name','position','team','nationality','fbrefMatchId','age']]
    fbref_players = fbref_players.merge(fbref_MatchInfos[['match_date','fbrefMatchId']], on='fbrefMatchId', how = 'inner')
    fbref_players['player_name'] = fbref_players['player_name'].astype('str')
    fbref_players['match_date'] = fbref_players['match_date'].astype('datetime64[ns]')
    player_attr['update_date'] = player_attr['update_date'].astype('datetime64[ns]')
    fbref_players['age'] = fbref_players['age'].astype('str')
    

MergedSoFifaFbref(fbref_MatchInfos,fbref_MatchPlayerStats,player_attr)

In [69]:
fbref_MatchInfos['match_date'] = fbref_MatchInfos['match_date'].astype('datetime64[ns]')
fbref_MatchInfos['match_date'][1]

Timestamp('2020-07-26 00:00:00')

In [63]:

# names = ['Troy','Deeney','askjd']
# all([name in ['Troy Deeney'] for name in names])
print(fbref_MatchInfos.columns.values.tolist())


['attendance', 'away_team', 'fbrefMatchId', 'fbrefURL', 'home_team', 'leauge', 'match_date', 'match_date_str', 'match_week', 'officials', 'season', 'venue', 'venue_time']
